In [2]:
import sys
sys.path.insert(1, '/scratch/cinthiasouza/mv-text-summarizer')

import itertools
import re

import glob, os
import pandas as pd
import json
#import spacy
import nltk
import numpy as np
import json
#import smogn
import seaborn as sns
import pickle

import joblib
from joblib import Parallel, delayed

from bs4 import BeautifulSoup
from pysbd.utils import PySBDFactory
import math

from sumeval.metrics.rouge import RougeCalculator
rouge = RougeCalculator(stopwords=True, lang="en")
import matplotlib.pyplot as plt
import random

from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.preprocessing import StandardScaler
from timeit import default_timer as timer 
from sklearn.metrics import matthews_corrcoef
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from catboost import CatBoostClassifier


#!python -m spacy download en_core_web_sm
#nlp_sm = spacy.load('en_core_web_sm')

#import en_core_web_sm
#nlp_md = en_core_web_sm.load()

#import en_core_web_md
#nlp_md = en_core_web_md.load()
#!python -m spacy download en_core_web_md
#nlp_md = spacy.load('en_core_web_md')

import warnings
warnings.filterwarnings("ignore")

path_base = "/scratch/cinthiasouza/mv-text-summarizer"
path_to_read="/scratch/cinthiasouza/mv-text-summarizer/result/{}/{}_*.csv"

In [5]:
%load_ext autoreload
%autoreload 2

#from src import preprocess
#from src import extract_features
#from src import tokenizer
#from src import create_features_df
#from src import transform_data
#from src import loader
#from src import utils
from src import tunning_hyperparametrs as th
from src import ensemble_tree_models as classifiers
from src import utils_classification as utils_clf
from src import evaluate_classifiers as ev
#from src import prepare_data
#from src import display_results as dr

import joblib
from joblib import Parallel, delayed

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Load Features

In [ ]:
"""import random

features_intro, scores_intro = loader.read_features(path="../result/introduction/features_*.csv")
features_mat, scores_mat = loader.read_features(path="../result/materials/features_*.csv")
features_conc, scores_conc = loader.read_features(path="../result/conclusion/features_*.csv")

intro = pd.unique(features_intro['articles'])
mat = pd.unique(features_mat['articles'])
conc = pd.unique(features_conc['articles'])

comuns = list((set(intro) & set(mat)) & set(conc))

valid_len = int(len(comuns)*0.2)
summ_items = random.sample(comuns, valid_len)

df = pd.DataFrame({'summ': summ_items})
df.to_csv("indices_summ.csv", index=False)"""

In [47]:
def main(path_to_read, name_csv="features", format_dataset=True, verbose=True):
    
    train_columns = ['text_rank', 'lex_rank', 'count_one_gram', 'count_two_gram',
       'count_three_gram', 'count_article_keywords',
       'tf-isf', 'position_score', 'paragraph_score',
       'length_score', 'pos_score', 'ner_score', 'dist_centroid']
    
    under_columns = ['sentences', 'articles', 'text_rank', 'lex_rank', 'count_one_gram', 'count_two_gram',
       'count_three_gram', 'count_article_keywords',
       'tf-isf', 'position_score', 'paragraph_score',
       'length_score', 'pos_score', 'ner_score', 'dist_centroid', 'rouge_1', 'bin']

    sections=['introduction', 'materials', 'conclusion', 'concat']
    #sections=[ 'introduction']

    if format_dataset:
        if verbose:
            print("Preparando dataset para os classificadores")
        dataset = prepare_data.main_create_dataset(
            train_columns, under_columns, sections, path_to_read, name_csv)
        #utils.,save_json(dataset, name='dataset', path=path)
    else:
        if verbose:
            print("Carregando dataset")
        dataset = utils.load_json(name='dataset', path=path)
    
    if verbose:
        print("Treinamento dos modelos")
        
    with open('dataset_{}.pkl'.format(name_csv), 'wb') as fp:
        pickle.dump(dataset, fp, protocol=pickle.HIGHEST_PROTOCOL)
        
    return dataset

In [ ]:
if __name__ == '__main__':

    parser = argparse.ArgumentParser()
    parser.add_argument('--path', "-p",required=True)
    parser.add_argument('--format_dataset', "-f",required=True)
     
    args = parser.parse_args()

    columns_name = ['text_rank', 'lex_rank', 'count_one_gram',
        'count_article_keywords',
       'tf-isf', 'position_score', 'paragraph_score',
       'length_score', 'pos_score', 'ner_score', 'dist_centroid']

    sections=['introduction', 'materials', 'conclusion', 'concat']

In [51]:
dataset  = main(verbose=True, path_to_read=path_to_read, name_csv='features')

Preparando dataset para os classificadores
924
Treinamento dos modelos


In [6]:
with open('autoencoder_64dim/dataset_{}.pkl'.format('features'), 'rb') as fp:
    dataset = pickle.load(fp)

sections=['introduction', 'materials', 'conclusion', 'concat']

In [36]:
folder_to_save = 'mv_tunning'
path_to_save = "/scratch/cinthiasouza/mv-text-summarizer/notebook/{}".format(folder_to_save)

## Randomized Search -  CV 5 Folds

In [37]:
parameters_tunning = {
    
 'rf': {'n_estimators': [10, 25, 50, 100],
              'min_samples_leaf':[2500, 5000, 1000],
              'min_samples_split':[5000, 10000, 2000],
              'max_depth':[2, 3, 5, 10]
              },
 'gb': {'n_estimators': [10, 25, 50, 100],
              'min_samples_leaf':[2500, 5000, 1000],
              'min_samples_split':[5000, 10000, 2000],
              'max_depth':[2, 3, 5, 10]
              },
'cb': {'iterations': [10, 25, 50, 100],
            'learning_rate': [0.01],
            'depth': [2, 3, 5, 10],
            'min_data_in_leaf':[2500, 5000, 1000]},
 'knn':  {'n_neighbors': [3, 5, 10]},
    
 'ab': {'n_estimators': [10, 25, 50, 100]}}


In [99]:
th.pipeline_tunning(dataset, {'cb': CatBoostClassifier()},
        sections, parameters_tunning, path_to_save, 0, 2)

0:	learn: 0.6915987	total: 224ms	remaining: 2.02s
1:	learn: 0.6900906	total: 230ms	remaining: 919ms
2:	learn: 0.6885893	total: 235ms	remaining: 547ms
3:	learn: 0.6871090	total: 240ms	remaining: 359ms
4:	learn: 0.6857199	total: 243ms	remaining: 243ms
5:	learn: 0.6843751	total: 246ms	remaining: 164ms
6:	learn: 0.6829725	total: 249ms	remaining: 107ms
7:	learn: 0.6816586	total: 252ms	remaining: 63ms
8:	learn: 0.6803522	total: 255ms	remaining: 28.3ms
9:	learn: 0.6790008	total: 258ms	remaining: 0us
0:	learn: 0.6915984	total: 4.43ms	remaining: 39.8ms
1:	learn: 0.6900937	total: 6.79ms	remaining: 27.2ms
2:	learn: 0.6886066	total: 9.83ms	remaining: 22.9ms
3:	learn: 0.6871408	total: 12.9ms	remaining: 19.4ms
4:	learn: 0.6857677	total: 16.1ms	remaining: 16.1ms
5:	learn: 0.6844271	total: 19.3ms	remaining: 12.8ms
6:	learn: 0.6830502	total: 22.1ms	remaining: 9.47ms
7:	learn: 0.6817639	total: 24.7ms	remaining: 6.17ms
8:	learn: 0.6804484	total: 27.2ms	remaining: 3.03ms
9:	learn: 0.6791848	total: 30.2ms	

0:	learn: 0.6915984	total: 4.88ms	remaining: 117ms
1:	learn: 0.6900937	total: 8.83ms	remaining: 102ms
2:	learn: 0.6886066	total: 12ms	remaining: 88ms
3:	learn: 0.6871408	total: 14.9ms	remaining: 78.3ms
4:	learn: 0.6857677	total: 17.8ms	remaining: 71.1ms
5:	learn: 0.6844271	total: 20.7ms	remaining: 65.6ms
6:	learn: 0.6830502	total: 23.7ms	remaining: 61ms
7:	learn: 0.6817639	total: 26.6ms	remaining: 56.5ms
8:	learn: 0.6804484	total: 29.6ms	remaining: 52.6ms
9:	learn: 0.6791848	total: 32.4ms	remaining: 48.6ms
10:	learn: 0.6778840	total: 35.3ms	remaining: 44.9ms
11:	learn: 0.6766217	total: 38.4ms	remaining: 41.6ms
12:	learn: 0.6753646	total: 41.2ms	remaining: 38.1ms
13:	learn: 0.6741354	total: 44.1ms	remaining: 34.7ms
14:	learn: 0.6730000	total: 47.1ms	remaining: 31.4ms
15:	learn: 0.6718379	total: 49.5ms	remaining: 27.9ms
16:	learn: 0.6707178	total: 52.5ms	remaining: 24.7ms
17:	learn: 0.6695707	total: 55.1ms	remaining: 21.4ms
18:	learn: 0.6684708	total: 57.6ms	remaining: 18.2ms
19:	learn: 

0:	learn: 0.6916255	total: 4.99ms	remaining: 120ms
1:	learn: 0.6902412	total: 9.03ms	remaining: 104ms
2:	learn: 0.6887472	total: 12.6ms	remaining: 92.2ms
3:	learn: 0.6872776	total: 16.5ms	remaining: 86.6ms
4:	learn: 0.6858756	total: 19.7ms	remaining: 78.8ms
5:	learn: 0.6845215	total: 22.7ms	remaining: 71.8ms
6:	learn: 0.6831492	total: 25.4ms	remaining: 65.4ms
7:	learn: 0.6818347	total: 28.3ms	remaining: 60.1ms
8:	learn: 0.6805039	total: 30.8ms	remaining: 54.8ms
9:	learn: 0.6791739	total: 33.5ms	remaining: 50.3ms
10:	learn: 0.6778728	total: 36.3ms	remaining: 46.3ms
11:	learn: 0.6766005	total: 39.2ms	remaining: 42.4ms
12:	learn: 0.6753609	total: 41.9ms	remaining: 38.6ms
13:	learn: 0.6741974	total: 44.8ms	remaining: 35.2ms
14:	learn: 0.6730455	total: 47.8ms	remaining: 31.9ms
15:	learn: 0.6718780	total: 50.6ms	remaining: 28.4ms
16:	learn: 0.6707139	total: 53.1ms	remaining: 25ms
17:	learn: 0.6695595	total: 55.9ms	remaining: 21.7ms
18:	learn: 0.6684404	total: 58.5ms	remaining: 18.5ms
19:	lea

0:	learn: 0.6915987	total: 2.91ms	remaining: 143ms
1:	learn: 0.6900906	total: 6.46ms	remaining: 155ms
2:	learn: 0.6885893	total: 10.6ms	remaining: 166ms
3:	learn: 0.6871090	total: 14.7ms	remaining: 169ms
4:	learn: 0.6857199	total: 17.9ms	remaining: 161ms
5:	learn: 0.6843751	total: 20.6ms	remaining: 151ms
6:	learn: 0.6829725	total: 23.8ms	remaining: 146ms
7:	learn: 0.6816586	total: 26.4ms	remaining: 138ms
8:	learn: 0.6803522	total: 29.3ms	remaining: 133ms
9:	learn: 0.6790008	total: 32.1ms	remaining: 128ms
10:	learn: 0.6776784	total: 34.6ms	remaining: 123ms
11:	learn: 0.6763936	total: 37.1ms	remaining: 117ms
12:	learn: 0.6751212	total: 39.9ms	remaining: 113ms
13:	learn: 0.6738855	total: 42.8ms	remaining: 110ms
14:	learn: 0.6726723	total: 45.6ms	remaining: 106ms
15:	learn: 0.6714937	total: 48.1ms	remaining: 102ms
16:	learn: 0.6703585	total: 50.6ms	remaining: 98.1ms
17:	learn: 0.6692041	total: 53ms	remaining: 94.1ms
18:	learn: 0.6680764	total: 55.7ms	remaining: 90.8ms
19:	learn: 0.6669772	

0:	learn: 0.6915928	total: 4.22ms	remaining: 207ms
1:	learn: 0.6901933	total: 7.93ms	remaining: 190ms
2:	learn: 0.6886811	total: 11.5ms	remaining: 180ms
3:	learn: 0.6872782	total: 15.3ms	remaining: 176ms
4:	learn: 0.6858629	total: 18.3ms	remaining: 165ms
5:	learn: 0.6844511	total: 21.4ms	remaining: 157ms
6:	learn: 0.6830613	total: 24ms	remaining: 148ms
7:	learn: 0.6817167	total: 26.9ms	remaining: 141ms
8:	learn: 0.6803879	total: 29.6ms	remaining: 135ms
9:	learn: 0.6790396	total: 32.5ms	remaining: 130ms
10:	learn: 0.6777144	total: 35.1ms	remaining: 125ms
11:	learn: 0.6764272	total: 37.8ms	remaining: 120ms
12:	learn: 0.6751567	total: 40.3ms	remaining: 115ms
13:	learn: 0.6739178	total: 42.6ms	remaining: 110ms
14:	learn: 0.6727531	total: 45.3ms	remaining: 106ms
15:	learn: 0.6715452	total: 48ms	remaining: 102ms
16:	learn: 0.6703697	total: 50.9ms	remaining: 98.7ms
17:	learn: 0.6692123	total: 53.5ms	remaining: 95.2ms
18:	learn: 0.6680930	total: 55.9ms	remaining: 91.2ms
19:	learn: 0.6669644	to

...

74:	learn: 0.5995876	total: 2.57s	remaining: 857ms
75:	learn: 0.5989387	total: 2.6s	remaining: 822ms
76:	learn: 0.5982739	total: 2.67s	remaining: 797ms
77:	learn: 0.5976096	total: 2.71s	remaining: 765ms
78:	learn: 0.5969843	total: 2.74s	remaining: 729ms
79:	learn: 0.5962903	total: 2.81s	remaining: 702ms
80:	learn: 0.5956131	total: 2.84s	remaining: 666ms
81:	learn: 0.5949551	total: 2.88s	remaining: 632ms
82:	learn: 0.5943254	total: 2.91s	remaining: 596ms
83:	learn: 0.5936976	total: 2.96s	remaining: 564ms
84:	learn: 0.5931201	total: 3.01s	remaining: 531ms
85:	learn: 0.5924951	total: 3.06s	remaining: 498ms
86:	learn: 0.5918603	total: 3.1s	remaining: 464ms
87:	learn: 0.5912946	total: 3.15s	remaining: 430ms
88:	learn: 0.5907270	total: 3.17s	remaining: 392ms
89:	learn: 0.5901349	total: 3.21s	remaining: 356ms
90:	learn: 0.5895570	total: 3.26s	remaining: 322ms
91:	learn: 0.5889834	total: 3.29s	remaining: 286ms
92:	learn: 0.5884552	total: 3.31s	remaining: 249ms
93:	learn: 0.5879109	total: 3.34s

38:	learn: 0.6315892	total: 1.56s	remaining: 2.43s
39:	learn: 0.6304547	total: 1.59s	remaining: 2.39s
40:	learn: 0.6293141	total: 1.63s	remaining: 2.34s
41:	learn: 0.6282518	total: 1.66s	remaining: 2.29s
42:	learn: 0.6271776	total: 1.7s	remaining: 2.25s
43:	learn: 0.6261237	total: 1.73s	remaining: 2.2s
44:	learn: 0.6251351	total: 1.76s	remaining: 2.15s
45:	learn: 0.6240899	total: 1.78s	remaining: 2.09s
46:	learn: 0.6230527	total: 1.81s	remaining: 2.04s
47:	learn: 0.6221110	total: 1.83s	remaining: 1.99s
48:	learn: 0.6211017	total: 1.86s	remaining: 1.94s
49:	learn: 0.6201373	total: 1.89s	remaining: 1.89s
50:	learn: 0.6191683	total: 1.91s	remaining: 1.83s
51:	learn: 0.6182212	total: 1.94s	remaining: 1.79s
52:	learn: 0.6172655	total: 1.98s	remaining: 1.75s
53:	learn: 0.6164035	total: 2.02s	remaining: 1.72s
54:	learn: 0.6154720	total: 2.06s	remaining: 1.68s
55:	learn: 0.6145784	total: 2.09s	remaining: 1.64s
56:	learn: 0.6137303	total: 2.14s	remaining: 1.61s
57:	learn: 0.6128502	total: 2.18s

0:	learn: 0.6909604	total: 39.4ms	remaining: 3.9s
1:	learn: 0.6888643	total: 82.2ms	remaining: 4.03s
2:	learn: 0.6868315	total: 131ms	remaining: 4.24s
3:	learn: 0.6848831	total: 169ms	remaining: 4.05s
4:	learn: 0.6829495	total: 219ms	remaining: 4.17s
5:	learn: 0.6810051	total: 250ms	remaining: 3.92s
6:	learn: 0.6790723	total: 276ms	remaining: 3.66s
7:	learn: 0.6772964	total: 323ms	remaining: 3.72s
8:	learn: 0.6754691	total: 418ms	remaining: 4.23s
9:	learn: 0.6737270	total: 452ms	remaining: 4.07s
10:	learn: 0.6719424	total: 481ms	remaining: 3.9s
11:	learn: 0.6702500	total: 524ms	remaining: 3.84s
12:	learn: 0.6684925	total: 565ms	remaining: 3.78s
13:	learn: 0.6667547	total: 610ms	remaining: 3.75s
14:	learn: 0.6651153	total: 642ms	remaining: 3.64s
15:	learn: 0.6634649	total: 679ms	remaining: 3.56s
16:	learn: 0.6617934	total: 705ms	remaining: 3.44s
17:	learn: 0.6601384	total: 755ms	remaining: 3.44s
18:	learn: 0.6585344	total: 794ms	remaining: 3.38s
19:	learn: 0.6569701	total: 837ms	remaini

65:	learn: 0.6062312	total: 2.6s	remaining: 1.34s
66:	learn: 0.6054873	total: 2.64s	remaining: 1.3s
67:	learn: 0.6047322	total: 2.67s	remaining: 1.26s
68:	learn: 0.6039501	total: 2.7s	remaining: 1.21s
69:	learn: 0.6032359	total: 2.74s	remaining: 1.17s
70:	learn: 0.6024727	total: 2.78s	remaining: 1.14s
71:	learn: 0.6017396	total: 2.82s	remaining: 1.1s
72:	learn: 0.6010400	total: 2.86s	remaining: 1.06s
73:	learn: 0.6003053	total: 2.91s	remaining: 1.02s
74:	learn: 0.5995876	total: 2.95s	remaining: 983ms
75:	learn: 0.5989387	total: 3s	remaining: 947ms
76:	learn: 0.5982739	total: 3.04s	remaining: 910ms
77:	learn: 0.5976096	total: 3.08s	remaining: 868ms
78:	learn: 0.5969843	total: 3.1s	remaining: 825ms
79:	learn: 0.5962903	total: 3.13s	remaining: 783ms
80:	learn: 0.5956131	total: 3.16s	remaining: 741ms
81:	learn: 0.5949551	total: 3.2s	remaining: 703ms
82:	learn: 0.5943254	total: 3.24s	remaining: 663ms
83:	learn: 0.5936976	total: 3.27s	remaining: 623ms
84:	learn: 0.5931201	total: 3.29s	remain

29:	learn: 0.6424720	total: 1.22s	remaining: 2.86s
30:	learn: 0.6411814	total: 1.29s	remaining: 2.88s
31:	learn: 0.6398689	total: 1.37s	remaining: 2.92s
32:	learn: 0.6385747	total: 1.43s	remaining: 2.91s
33:	learn: 0.6373530	total: 1.52s	remaining: 2.94s
34:	learn: 0.6361131	total: 1.54s	remaining: 2.86s
35:	learn: 0.6349431	total: 1.57s	remaining: 2.8s
36:	learn: 0.6336792	total: 1.6s	remaining: 2.73s
37:	learn: 0.6324878	total: 1.63s	remaining: 2.66s
38:	learn: 0.6313479	total: 1.66s	remaining: 2.59s
39:	learn: 0.6302180	total: 1.69s	remaining: 2.53s
40:	learn: 0.6290989	total: 1.73s	remaining: 2.48s
41:	learn: 0.6279787	total: 1.77s	remaining: 2.44s
42:	learn: 0.6269070	total: 1.82s	remaining: 2.41s
43:	learn: 0.6258148	total: 1.86s	remaining: 2.37s
44:	learn: 0.6247791	total: 1.9s	remaining: 2.32s
45:	learn: 0.6237107	total: 1.95s	remaining: 2.28s
46:	learn: 0.6226669	total: 1.98s	remaining: 2.23s
47:	learn: 0.6217044	total: 2.03s	remaining: 2.2s
48:	learn: 0.6207099	total: 2.08s	r

In [74]:
l1 = Queue()
p1 = Process(
    target=th.pipeline_tunning, args=(
        dataset, {'knn': KNeighborsClassifier()},
        sections, parameters_tunning, path_to_save, -2, 2))

l2 = Queue()
p2 = Process(
    target=th.pipeline_tunning, args=(
        dataset, {'rf': RandomForestClassifier()},
        sections, parameters_tunning, path_to_save, -2, 2))

l3 = Queue()
p3 = Process(
    target=th.pipeline_tunning, args=(
        dataset, {'ab': AdaBoostClassifier()},
        sections, parameters_tunning, path_to_save, -2, 2))
l5 = Queue()
p5 = Process(
    target=th.pipeline_tunning, args=(
        dataset, {'gb': GradientBoostingClassifier()},
        sections, parameters_tunning, path_to_save, -2, 2))

l6 = Queue()
p6 = Process(
    target=th.pipeline_tunning, args=(
        dataset, {'cb': CatBoostClassifier()},
        sections, parameters_tunning, path_to_save, -2, 2))



p5.start()
p6.start()
p3.start()
p2.start() 
p1.start()

0:	learn: 0.6922957	total: 153ms	remaining: 1.37s
1:	learn: 0.6914646	total: 164ms	remaining: 657ms
2:	learn: 0.6906818	total: 183ms	remaining: 427ms
3:	learn: 0.6898751	total: 197ms	remaining: 296ms
4:	learn: 0.6891026	total: 211ms	remaining: 211ms
5:	learn: 0.6882698	total: 225ms	remaining: 150ms
6:	learn: 0.6874888	total: 281ms	remaining: 120ms
7:	learn: 0.6867375	total: 317ms	remaining: 79.2ms
8:	learn: 0.6859483	total: 344ms	remaining: 38.2ms
9:	learn: 0.6852430	total: 358ms	remaining: 0us
0:	learn: 0.6923003	total: 11.8ms	remaining: 107ms
1:	learn: 0.6913924	total: 23.1ms	remaining: 92.3ms
2:	learn: 0.6905677	total: 38ms	remaining: 88.8ms
3:	learn: 0.6897247	total: 52ms	remaining: 78.1ms
4:	learn: 0.6888969	total: 68.3ms	remaining: 68.3ms
5:	learn: 0.6881050	total: 80.3ms	remaining: 53.6ms
6:	learn: 0.6873058	total: 94.5ms	remaining: 40.5ms
7:	learn: 0.6865634	total: 108ms	remaining: 26.9ms
8:	learn: 0.6857979	total: 120ms	remaining: 13.4ms
9:	learn: 0.6850532	total: 133ms	remain

13:	learn: 0.6824820	total: 400ms	remaining: 315ms
14:	learn: 0.6818050	total: 412ms	remaining: 275ms
15:	learn: 0.6811453	total: 423ms	remaining: 238ms
16:	learn: 0.6804265	total: 452ms	remaining: 213ms
17:	learn: 0.6797826	total: 546ms	remaining: 212ms
18:	learn: 0.6791141	total: 565ms	remaining: 178ms
19:	learn: 0.6784612	total: 601ms	remaining: 150ms
20:	learn: 0.6778786	total: 612ms	remaining: 117ms
21:	learn: 0.6772830	total: 624ms	remaining: 85ms
22:	learn: 0.6766358	total: 660ms	remaining: 57.4ms
23:	learn: 0.6760734	total: 687ms	remaining: 28.6ms
24:	learn: 0.6754435	total: 726ms	remaining: 0us
0:	learn: 0.6923003	total: 10.2ms	remaining: 245ms
1:	learn: 0.6913924	total: 43.5ms	remaining: 501ms
2:	learn: 0.6905677	total: 62.1ms	remaining: 455ms
3:	learn: 0.6897247	total: 137ms	remaining: 717ms
4:	learn: 0.6888969	total: 150ms	remaining: 599ms
5:	learn: 0.6881050	total: 162ms	remaining: 513ms
6:	learn: 0.6873058	total: 173ms	remaining: 446ms
7:	learn: 0.6865634	total: 186ms	rem

24:	learn: 0.6752765	total: 367ms	remaining: 0us
0:	learn: 0.6923078	total: 11.4ms	remaining: 273ms
1:	learn: 0.6914416	total: 24.7ms	remaining: 284ms
2:	learn: 0.6906375	total: 35.2ms	remaining: 258ms
3:	learn: 0.6897899	total: 44.8ms	remaining: 235ms
4:	learn: 0.6889971	total: 54.3ms	remaining: 217ms
5:	learn: 0.6882471	total: 64.6ms	remaining: 205ms
6:	learn: 0.6874703	total: 76ms	remaining: 195ms
7:	learn: 0.6867012	total: 87.3ms	remaining: 185ms
8:	learn: 0.6859045	total: 99ms	remaining: 176ms
9:	learn: 0.6851714	total: 110ms	remaining: 166ms
10:	learn: 0.6844816	total: 122ms	remaining: 155ms
11:	learn: 0.6837776	total: 134ms	remaining: 145ms
12:	learn: 0.6830954	total: 145ms	remaining: 134ms
13:	learn: 0.6823650	total: 156ms	remaining: 122ms
14:	learn: 0.6817045	total: 167ms	remaining: 111ms
15:	learn: 0.6810500	total: 179ms	remaining: 101ms
16:	learn: 0.6804424	total: 191ms	remaining: 89.9ms
17:	learn: 0.6798313	total: 201ms	remaining: 78.2ms
18:	learn: 0.6792180	total: 213ms	re

11:	learn: 0.6836924	total: 338ms	remaining: 366ms
12:	learn: 0.6829461	total: 348ms	remaining: 322ms
13:	learn: 0.6822594	total: 365ms	remaining: 287ms
14:	learn: 0.6816101	total: 376ms	remaining: 251ms
15:	learn: 0.6809605	total: 430ms	remaining: 242ms
16:	learn: 0.6802396	total: 474ms	remaining: 223ms
17:	learn: 0.6795272	total: 530ms	remaining: 206ms
18:	learn: 0.6789055	total: 544ms	remaining: 172ms
19:	learn: 0.6782894	total: 568ms	remaining: 142ms
20:	learn: 0.6776975	total: 595ms	remaining: 113ms
21:	learn: 0.6770296	total: 607ms	remaining: 82.8ms
22:	learn: 0.6764394	total: 620ms	remaining: 53.9ms
23:	learn: 0.6758713	total: 665ms	remaining: 27.7ms
24:	learn: 0.6753004	total: 677ms	remaining: 0us
0:	learn: 0.6923142	total: 15.9ms	remaining: 381ms
1:	learn: 0.6915106	total: 31.5ms	remaining: 362ms
2:	learn: 0.6906973	total: 41.8ms	remaining: 307ms
3:	learn: 0.6898673	total: 91.9ms	remaining: 482ms
4:	learn: 0.6890619	total: 104ms	remaining: 417ms
5:	learn: 0.6882697	total: 126m

22:	learn: 0.6767223	total: 393ms	remaining: 462ms
23:	learn: 0.6761032	total: 408ms	remaining: 442ms
24:	learn: 0.6755317	total: 422ms	remaining: 422ms
25:	learn: 0.6749705	total: 455ms	remaining: 420ms
26:	learn: 0.6744072	total: 467ms	remaining: 398ms
27:	learn: 0.6738515	total: 480ms	remaining: 377ms
28:	learn: 0.6732597	total: 512ms	remaining: 371ms
29:	learn: 0.6727324	total: 590ms	remaining: 394ms
30:	learn: 0.6722182	total: 618ms	remaining: 379ms
31:	learn: 0.6716758	total: 638ms	remaining: 359ms
32:	learn: 0.6711859	total: 664ms	remaining: 342ms
33:	learn: 0.6706988	total: 676ms	remaining: 318ms
34:	learn: 0.6702281	total: 691ms	remaining: 296ms
35:	learn: 0.6697536	total: 710ms	remaining: 276ms
36:	learn: 0.6692898	total: 721ms	remaining: 253ms
37:	learn: 0.6688066	total: 738ms	remaining: 233ms
38:	learn: 0.6683205	total: 753ms	remaining: 212ms
39:	learn: 0.6679035	total: 766ms	remaining: 191ms
40:	learn: 0.6674506	total: 807ms	remaining: 177ms
41:	learn: 0.6669877	total: 850

...

84:	learn: 0.6469074	total: 1m 22s	remaining: 14.5s
85:	learn: 0.6466891	total: 1m 23s	remaining: 13.5s
86:	learn: 0.6464655	total: 1m 24s	remaining: 12.6s
87:	learn: 0.6462452	total: 1m 25s	remaining: 11.6s
88:	learn: 0.6460164	total: 1m 26s	remaining: 10.6s
89:	learn: 0.6458229	total: 1m 27s	remaining: 9.69s
90:	learn: 0.6456275	total: 1m 28s	remaining: 8.71s
91:	learn: 0.6454198	total: 1m 29s	remaining: 7.74s
92:	learn: 0.6452223	total: 1m 29s	remaining: 6.77s
93:	learn: 0.6450054	total: 1m 30s	remaining: 5.8s
94:	learn: 0.6448094	total: 1m 31s	remaining: 4.83s
95:	learn: 0.6445995	total: 1m 32s	remaining: 3.86s
96:	learn: 0.6444084	total: 1m 33s	remaining: 2.9s
97:	learn: 0.6442330	total: 1m 34s	remaining: 1.93s
98:	learn: 0.6440513	total: 1m 35s	remaining: 967ms
99:	learn: 0.6438695	total: 1m 36s	remaining: 0us
0:	learn: 0.6920619	total: 896ms	remaining: 1m 28s
1:	learn: 0.6910300	total: 1.9s	remaining: 1m 32s
2:	learn: 0.6900115	total: 2.83s	remaining: 1m 31s
3:	learn: 0.6890285	

44:	learn: 0.6597918	total: 43.7s	remaining: 53.4s
45:	learn: 0.6593245	total: 44.6s	remaining: 52.4s
46:	learn: 0.6588904	total: 45.5s	remaining: 51.3s
47:	learn: 0.6584371	total: 46.5s	remaining: 50.4s
48:	learn: 0.6579876	total: 47.4s	remaining: 49.3s
49:	learn: 0.6575290	total: 48.3s	remaining: 48.3s
50:	learn: 0.6571067	total: 49.3s	remaining: 47.4s
51:	learn: 0.6566740	total: 50.3s	remaining: 46.4s
52:	learn: 0.6562663	total: 51.2s	remaining: 45.4s
53:	learn: 0.6558730	total: 52.1s	remaining: 44.4s
54:	learn: 0.6554947	total: 53s	remaining: 43.3s
55:	learn: 0.6551048	total: 53.9s	remaining: 42.4s
56:	learn: 0.6547141	total: 54.8s	remaining: 41.4s
57:	learn: 0.6543455	total: 55.7s	remaining: 40.4s
58:	learn: 0.6539702	total: 56.6s	remaining: 39.4s
59:	learn: 0.6536110	total: 57.6s	remaining: 38.4s
60:	learn: 0.6532653	total: 58.6s	remaining: 37.5s
61:	learn: 0.6529357	total: 59.6s	remaining: 36.5s
62:	learn: 0.6525928	total: 1m	remaining: 35.5s
63:	learn: 0.6522419	total: 1m 1s	re

5:	learn: 0.6871682	total: 5.75s	remaining: 1m 30s
6:	learn: 0.6862231	total: 6.72s	remaining: 1m 29s
7:	learn: 0.6852718	total: 7.82s	remaining: 1m 29s
8:	learn: 0.6844066	total: 8.83s	remaining: 1m 29s
9:	learn: 0.6835034	total: 9.84s	remaining: 1m 28s
10:	learn: 0.6826397	total: 10.8s	remaining: 1m 27s
11:	learn: 0.6818423	total: 11.7s	remaining: 1m 25s
12:	learn: 0.6809915	total: 12.7s	remaining: 1m 25s
13:	learn: 0.6802051	total: 13.7s	remaining: 1m 24s
14:	learn: 0.6794023	total: 14.6s	remaining: 1m 22s
15:	learn: 0.6786414	total: 15.5s	remaining: 1m 21s
16:	learn: 0.6778733	total: 16.4s	remaining: 1m 20s
17:	learn: 0.6770819	total: 17.4s	remaining: 1m 19s
18:	learn: 0.6763308	total: 18.4s	remaining: 1m 18s
19:	learn: 0.6756018	total: 19.3s	remaining: 1m 17s
20:	learn: 0.6748762	total: 20.3s	remaining: 1m 16s
21:	learn: 0.6741865	total: 21.2s	remaining: 1m 15s
22:	learn: 0.6734992	total: 22.2s	remaining: 1m 14s
23:	learn: 0.6727853	total: 23.1s	remaining: 1m 13s
24:	learn: 0.6721

66:	learn: 0.6517958	total: 1m 4s	remaining: 31.8s
67:	learn: 0.6514831	total: 1m 5s	remaining: 30.9s
68:	learn: 0.6511812	total: 1m 6s	remaining: 29.9s
69:	learn: 0.6508730	total: 1m 7s	remaining: 29.1s
70:	learn: 0.6505712	total: 1m 8s	remaining: 28.1s
71:	learn: 0.6502813	total: 1m 9s	remaining: 27.2s
72:	learn: 0.6499999	total: 1m 10s	remaining: 26.2s
73:	learn: 0.6497129	total: 1m 11s	remaining: 25.2s
74:	learn: 0.6494256	total: 1m 12s	remaining: 24.2s
75:	learn: 0.6491435	total: 1m 13s	remaining: 23.2s
76:	learn: 0.6488791	total: 1m 14s	remaining: 22.3s
77:	learn: 0.6486204	total: 1m 15s	remaining: 21.3s
78:	learn: 0.6483570	total: 1m 16s	remaining: 20.3s
79:	learn: 0.6481040	total: 1m 17s	remaining: 19.4s
80:	learn: 0.6478590	total: 1m 18s	remaining: 18.4s
81:	learn: 0.6476155	total: 1m 19s	remaining: 17.4s
82:	learn: 0.6473749	total: 1m 20s	remaining: 16.5s
83:	learn: 0.6471273	total: 1m 21s	remaining: 15.5s
84:	learn: 0.6469074	total: 1m 22s	remaining: 14.5s
85:	learn: 0.64668

26:	learn: 0.6698970	total: 27s	remaining: 1m 13s
27:	learn: 0.6692674	total: 28s	remaining: 1m 12s
28:	learn: 0.6686106	total: 28.9s	remaining: 1m 10s
29:	learn: 0.6679881	total: 29.9s	remaining: 1m 9s
30:	learn: 0.6673778	total: 30.8s	remaining: 1m 8s
31:	learn: 0.6667409	total: 31.7s	remaining: 1m 7s
32:	learn: 0.6661507	total: 32.7s	remaining: 1m 6s
33:	learn: 0.6655930	total: 33.7s	remaining: 1m 5s
34:	learn: 0.6650300	total: 34.5s	remaining: 1m 4s
35:	learn: 0.6644682	total: 35.5s	remaining: 1m 3s
36:	learn: 0.6639046	total: 36.5s	remaining: 1m 2s
37:	learn: 0.6633631	total: 37.4s	remaining: 1m 1s
38:	learn: 0.6628396	total: 38.3s	remaining: 59.9s
39:	learn: 0.6623179	total: 39.3s	remaining: 58.9s
40:	learn: 0.6617994	total: 40.2s	remaining: 57.8s
41:	learn: 0.6612821	total: 41.1s	remaining: 56.8s
42:	learn: 0.6607753	total: 42.1s	remaining: 55.8s
43:	learn: 0.6602853	total: 43.1s	remaining: 54.9s
44:	learn: 0.6597918	total: 44s	remaining: 53.8s
45:	learn: 0.6593245	total: 45s	re

In [98]:
sections=['conclusion']

In [95]:
from multiprocessing import Process, Queue

l4 = Queue()
p4 = Process(
    target=th.pipeline_tunning, args=(
        dataset, {'cb': CatBoostClassifier()},
        sections, parameters_tunning, path_to_save, 0, 2))


p4.start()   


0:	learn: 0.6915987	total: 92.6ms	remaining: 833ms
1:	learn: 0.6900906	total: 101ms	remaining: 405ms
2:	learn: 0.6885893	total: 105ms	remaining: 245ms
3:	learn: 0.6871090	total: 111ms	remaining: 167ms
4:	learn: 0.6857199	total: 120ms	remaining: 120ms
5:	learn: 0.6843751	total: 126ms	remaining: 84.2ms
6:	learn: 0.6829725	total: 179ms	remaining: 76.7ms
7:	learn: 0.6816586	total: 188ms	remaining: 46.9ms
8:	learn: 0.6803522	total: 202ms	remaining: 22.4ms
9:	learn: 0.6790008	total: 212ms	remaining: 0us
0:	learn: 0.6915984	total: 4.14ms	remaining: 37.3ms
1:	learn: 0.6900937	total: 7.34ms	remaining: 29.4ms
2:	learn: 0.6886066	total: 11.8ms	remaining: 27.6ms
3:	learn: 0.6871408	total: 14.9ms	remaining: 22.3ms
4:	learn: 0.6857677	total: 18.9ms	remaining: 18.9ms
5:	learn: 0.6844271	total: 22.2ms	remaining: 14.8ms
6:	learn: 0.6830502	total: 25.1ms	remaining: 10.8ms
7:	learn: 0.6817639	total: 30.5ms	remaining: 7.62ms
8:	learn: 0.6804484	total: 33.4ms	remaining: 3.71ms
9:	learn: 0.6791848	total: 36

10:	learn: 0.6776784	total: 43.4ms	remaining: 55.2ms
11:	learn: 0.6763936	total: 46.6ms	remaining: 50.5ms
12:	learn: 0.6751212	total: 50.2ms	remaining: 46.3ms
13:	learn: 0.6738855	total: 53.5ms	remaining: 42ms
14:	learn: 0.6726723	total: 57ms	remaining: 38ms
15:	learn: 0.6714937	total: 60.3ms	remaining: 33.9ms
16:	learn: 0.6703585	total: 63.3ms	remaining: 29.8ms
17:	learn: 0.6692041	total: 66.3ms	remaining: 25.8ms
18:	learn: 0.6680764	total: 69.6ms	remaining: 22ms
19:	learn: 0.6669772	total: 73.1ms	remaining: 18.3ms
20:	learn: 0.6658833	total: 76.4ms	remaining: 14.5ms
21:	learn: 0.6648453	total: 79.5ms	remaining: 10.8ms
22:	learn: 0.6638226	total: 82.9ms	remaining: 7.21ms
23:	learn: 0.6628354	total: 86.3ms	remaining: 3.6ms
24:	learn: 0.6617957	total: 91.1ms	remaining: 0us
0:	learn: 0.6915984	total: 3.92ms	remaining: 94.2ms
1:	learn: 0.6900937	total: 7.58ms	remaining: 87.2ms
2:	learn: 0.6886066	total: 10.9ms	remaining: 79.7ms
3:	learn: 0.6871408	total: 15.4ms	remaining: 81ms
4:	learn: 0

19:	learn: 0.6673556	total: 75.8ms	remaining: 18.9ms
20:	learn: 0.6662778	total: 78.6ms	remaining: 15ms
21:	learn: 0.6652461	total: 81.6ms	remaining: 11.1ms
22:	learn: 0.6642217	total: 84.7ms	remaining: 7.36ms
23:	learn: 0.6632332	total: 88ms	remaining: 3.66ms
24:	learn: 0.6622271	total: 91.5ms	remaining: 0us
0:	learn: 0.6915954	total: 4.07ms	remaining: 97.8ms
1:	learn: 0.6900904	total: 8.28ms	remaining: 95.3ms
2:	learn: 0.6885955	total: 11.3ms	remaining: 82.6ms
3:	learn: 0.6871081	total: 16.2ms	remaining: 84.8ms
4:	learn: 0.6857082	total: 19.4ms	remaining: 77.7ms
5:	learn: 0.6843633	total: 22.7ms	remaining: 71.8ms
6:	learn: 0.6829935	total: 25.9ms	remaining: 66.5ms
7:	learn: 0.6816595	total: 29ms	remaining: 61.6ms
8:	learn: 0.6803207	total: 32.1ms	remaining: 57ms
9:	learn: 0.6789838	total: 35.3ms	remaining: 52.9ms
10:	learn: 0.6776698	total: 38.3ms	remaining: 48.8ms
11:	learn: 0.6763973	total: 41.3ms	remaining: 44.8ms
12:	learn: 0.6751360	total: 44.4ms	remaining: 41ms
13:	learn: 0.673

3:	learn: 0.6872776	total: 14.3ms	remaining: 75.2ms
4:	learn: 0.6858756	total: 17.7ms	remaining: 70.9ms
5:	learn: 0.6845215	total: 21.2ms	remaining: 67ms
6:	learn: 0.6831492	total: 24.2ms	remaining: 62.2ms
7:	learn: 0.6818347	total: 30ms	remaining: 63.7ms
8:	learn: 0.6805039	total: 34.3ms	remaining: 61ms
9:	learn: 0.6791739	total: 37.6ms	remaining: 56.5ms
10:	learn: 0.6778728	total: 40.6ms	remaining: 51.6ms
11:	learn: 0.6766005	total: 43.7ms	remaining: 47.4ms
12:	learn: 0.6753609	total: 48.3ms	remaining: 44.6ms
13:	learn: 0.6741974	total: 51.6ms	remaining: 40.5ms
14:	learn: 0.6730455	total: 54.9ms	remaining: 36.6ms
15:	learn: 0.6718780	total: 58.2ms	remaining: 32.7ms
16:	learn: 0.6707139	total: 61.7ms	remaining: 29ms
17:	learn: 0.6695595	total: 65.3ms	remaining: 25.4ms
18:	learn: 0.6684404	total: 68.7ms	remaining: 21.7ms
19:	learn: 0.6673457	total: 72ms	remaining: 18ms
20:	learn: 0.6662512	total: 77.1ms	remaining: 14.7ms
21:	learn: 0.6652091	total: 82.2ms	remaining: 11.2ms
22:	learn: 0

12:	learn: 0.6751360	total: 51.2ms	remaining: 146ms
13:	learn: 0.6739072	total: 54.4ms	remaining: 140ms
14:	learn: 0.6726908	total: 58.9ms	remaining: 137ms
15:	learn: 0.6714951	total: 62.3ms	remaining: 132ms
16:	learn: 0.6703637	total: 71.3ms	remaining: 138ms
17:	learn: 0.6692120	total: 75.6ms	remaining: 134ms
18:	learn: 0.6681031	total: 106ms	remaining: 173ms
19:	learn: 0.6670124	total: 109ms	remaining: 164ms
20:	learn: 0.6659256	total: 113ms	remaining: 156ms
21:	learn: 0.6648852	total: 116ms	remaining: 148ms
22:	learn: 0.6638381	total: 123ms	remaining: 144ms
23:	learn: 0.6628538	total: 126ms	remaining: 137ms
24:	learn: 0.6618396	total: 129ms	remaining: 129ms
25:	learn: 0.6608280	total: 133ms	remaining: 122ms
26:	learn: 0.6598848	total: 140ms	remaining: 119ms
27:	learn: 0.6589013	total: 143ms	remaining: 113ms
28:	learn: 0.6579573	total: 146ms	remaining: 106ms
29:	learn: 0.6570315	total: 149ms	remaining: 99.6ms
30:	learn: 0.6561318	total: 153ms	remaining: 93.5ms
31:	learn: 0.6552533	to

...

6:	learn: 0.6791620	total: 153ms	remaining: 2.04s
7:	learn: 0.6772201	total: 177ms	remaining: 2.03s
8:	learn: 0.6753270	total: 199ms	remaining: 2.02s
9:	learn: 0.6736125	total: 227ms	remaining: 2.04s
10:	learn: 0.6718584	total: 250ms	remaining: 2.02s
11:	learn: 0.6702260	total: 272ms	remaining: 2s
12:	learn: 0.6685237	total: 293ms	remaining: 1.96s
13:	learn: 0.6667898	total: 316ms	remaining: 1.94s
14:	learn: 0.6651439	total: 339ms	remaining: 1.92s
15:	learn: 0.6635295	total: 360ms	remaining: 1.89s
16:	learn: 0.6618465	total: 383ms	remaining: 1.87s
17:	learn: 0.6601827	total: 405ms	remaining: 1.84s
18:	learn: 0.6586021	total: 426ms	remaining: 1.82s
19:	learn: 0.6570411	total: 451ms	remaining: 1.8s
20:	learn: 0.6554696	total: 473ms	remaining: 1.78s
21:	learn: 0.6539484	total: 498ms	remaining: 1.76s
22:	learn: 0.6523932	total: 520ms	remaining: 1.74s
23:	learn: 0.6509304	total: 542ms	remaining: 1.72s
24:	learn: 0.6494499	total: 566ms	remaining: 1.7s
25:	learn: 0.6480371	total: 600ms	remain

68:	learn: 0.6045623	total: 2.65s	remaining: 1.19s
69:	learn: 0.6039068	total: 2.67s	remaining: 1.14s
70:	learn: 0.6031434	total: 2.69s	remaining: 1.1s
71:	learn: 0.6024223	total: 2.71s	remaining: 1.05s
72:	learn: 0.6017306	total: 2.73s	remaining: 1.01s
73:	learn: 0.6010465	total: 2.75s	remaining: 968ms
74:	learn: 0.6003716	total: 2.78s	remaining: 925ms
75:	learn: 0.5996875	total: 2.8s	remaining: 884ms
76:	learn: 0.5990567	total: 2.82s	remaining: 842ms
77:	learn: 0.5983912	total: 2.84s	remaining: 801ms
78:	learn: 0.5977738	total: 2.86s	remaining: 761ms
79:	learn: 0.5970871	total: 2.88s	remaining: 721ms
80:	learn: 0.5964757	total: 2.9s	remaining: 682ms
81:	learn: 0.5958189	total: 2.93s	remaining: 642ms
82:	learn: 0.5951731	total: 2.95s	remaining: 604ms
83:	learn: 0.5946076	total: 2.97s	remaining: 566ms
84:	learn: 0.5940147	total: 2.99s	remaining: 528ms
85:	learn: 0.5933906	total: 3.02s	remaining: 491ms
86:	learn: 0.5927981	total: 3.04s	remaining: 454ms
87:	learn: 0.5922363	total: 3.06s	

30:	learn: 0.6414273	total: 1.55s	remaining: 3.45s
31:	learn: 0.6401067	total: 1.58s	remaining: 3.36s
32:	learn: 0.6388972	total: 1.66s	remaining: 3.37s
33:	learn: 0.6376689	total: 1.72s	remaining: 3.34s
34:	learn: 0.6364133	total: 1.77s	remaining: 3.29s
35:	learn: 0.6352250	total: 1.81s	remaining: 3.23s
36:	learn: 0.6339509	total: 1.88s	remaining: 3.2s
37:	learn: 0.6327432	total: 1.92s	remaining: 3.13s
38:	learn: 0.6315763	total: 1.96s	remaining: 3.06s
39:	learn: 0.6304111	total: 2.01s	remaining: 3.02s
40:	learn: 0.6292658	total: 2.05s	remaining: 2.94s
41:	learn: 0.6282022	total: 2.09s	remaining: 2.88s
42:	learn: 0.6271336	total: 2.12s	remaining: 2.81s
43:	learn: 0.6260328	total: 2.17s	remaining: 2.77s
44:	learn: 0.6250520	total: 2.22s	remaining: 2.72s
45:	learn: 0.6240095	total: 2.28s	remaining: 2.68s
46:	learn: 0.6229351	total: 2.33s	remaining: 2.63s
47:	learn: 0.6219765	total: 2.36s	remaining: 2.56s
48:	learn: 0.6209799	total: 2.38s	remaining: 2.48s
49:	learn: 0.6199944	total: 2.4s

92:	learn: 0.5883031	total: 2.02s	remaining: 152ms
93:	learn: 0.5877900	total: 2.04s	remaining: 130ms
94:	learn: 0.5872939	total: 2.06s	remaining: 108ms
95:	learn: 0.5867466	total: 2.08s	remaining: 86.6ms
96:	learn: 0.5861999	total: 2.1s	remaining: 64.9ms
97:	learn: 0.5856606	total: 2.12s	remaining: 43.3ms
98:	learn: 0.5851218	total: 2.14s	remaining: 21.6ms
99:	learn: 0.5846355	total: 2.16s	remaining: 0us
0:	learn: 0.6909238	total: 55.5ms	remaining: 5.5s
1:	learn: 0.6888198	total: 148ms	remaining: 7.26s
2:	learn: 0.6867891	total: 218ms	remaining: 7.04s
3:	learn: 0.6848072	total: 312ms	remaining: 7.5s
4:	learn: 0.6828720	total: 402ms	remaining: 7.63s
5:	learn: 0.6809649	total: 468ms	remaining: 7.33s
6:	learn: 0.6789791	total: 581ms	remaining: 7.71s
7:	learn: 0.6770347	total: 647ms	remaining: 7.45s
8:	learn: 0.6752095	total: 686ms	remaining: 6.93s
9:	learn: 0.6734940	total: 735ms	remaining: 6.62s
10:	learn: 0.6716466	total: 802ms	remaining: 6.49s
11:	learn: 0.6699266	total: 860ms	remaini

Process Process-16:


In [38]:
def load_rs_model(name_model, sections, path_to_read):
    
    rs_models = {}
    
    for section in sections:
        
        rs_models[section] = joblib.load('{}/search_{}_{}.pkl'.format(path_to_read, name_model, section))
        
    return rs_models

In [39]:
def get_scores(name_models, sections, path_to_read):

    results = {}
    
    for name_model in name_models:
        
        rs_models = load_rs_model(name_model, sections, path_to_read)
    
        aux  = { 'score_{}'.format(section): rs_models[section].best_score_ for section in sections}
        results[name_model] = aux
        
    return results

In [40]:
sections=['introduction', 'materials', 'conclusion']
name_models = ['knn', 'rf', 'ab', 'cb' , 'gb']

results = get_scores(name_models, sections, path_to_save)

## Results K-Fold Cross Validation

In [41]:
cv_results = pd.DataFrame(results).T
cv_results

score_introduction  score_materials  score_conclusion
knn            0.646071         0.692538          0.688620
rf             0.646440         0.683680          0.668149
ab             0.648216         0.685960          0.677509
cb             0.649478         0.698956          0.684064
gb             0.655811         0.687053          0.686473

In [79]:
cv_results = pd.DataFrame(results).T
cv_results

score_introduction  score_materials  score_conclusion
knn            0.646071         0.692538          0.688620
ab             0.648216         0.685960          0.677509
cb             0.649478         0.698956          0.684064

In [46]:
with open('mv_tunning/parameters.pkl', 'rb') as fp:
    parameters = pickle.load(fp)

In [47]:
parameters

{'knn': {'introduction': {'n_neighbors': 10},
  'materials': {'n_neighbors': 10},
  'conclusion': {'n_neighbors': 10}},
 'ab': {'introduction': {'n_estimators': 100},
  'materials': {'n_estimators': 10},
  'conclusion': {'n_estimators': 100}},
 'rf': {'introduction': {'n_estimators': 50,
   'min_samples_split': 2000,
   'min_samples_leaf': 1000,
   'max_depth': 10},
  'materials': {'n_estimators': 10,
   'min_samples_split': 2000,
   'min_samples_leaf': 1000,
   'max_depth': 2},
  'conclusion': {'n_estimators': 50,
   'min_samples_split': 2000,
   'min_samples_leaf': 1000,
   'max_depth': 10}},
 'gb': {'introduction': {'n_estimators': 100,
   'min_samples_split': 2000,
   'min_samples_leaf': 1000,
   'max_depth': 5},
  'materials': {'n_estimators': 100,
   'min_samples_split': 5000,
   'min_samples_leaf': 1000,
   'max_depth': 10},
  'conclusion': {'n_estimators': 100,
   'min_samples_split': 2000,
   'min_samples_leaf': 1000,
   'max_depth': 5}},
 'cb': {'introduction': {'min_data_in_

In [30]:
with open('sv_models/parameters.pkl', 'wb') as fp:
     pickle.dump(parameters, fp, protocol=pickle.HIGHEST_PROTOCOL)

## Hyperparameters

In [17]:
def get_models_rs(name_models, sections, path_to_read, verbose=False):

    searches = {}

    for name_model in name_models:

        aux = {}

        for section in sections:

            aux[section] = joblib.load('{}/search_{}_{}.pkl'.format(path_to_read, name_model, section))

            if verbose: 
                print(aux[section].best_params_)

        searches[name_model] = aux

    return searches


In [18]:
def get_dict_parameters(searches, name_models, sections):

    parameters = {}

    for name_model in name_models:

        aux = {}

        for section in sections:

            aux[section] = searches[name_model][section].best_params_

        parameters[name_model] = aux
    
    return parameters

In [20]:
sections=['introduction','materials', 'conclusion']
name_models = ['knn', 'rf', 'ab', 'cb' , 'gb']

In [21]:
searches = get_models_rs(name_models, sections, path_to_save)

In [22]:
parameters = get_dict_parameters(searches, name_models, sections)

## Train Test

In [33]:
path_to_save = "/scratch/cinthiasouza/mv-text-summarizer/notebook/{}".format('sv_models')

In [21]:
classifiers.pipeline_classifiers(
    dataset, parameters, sections, ['knn'], -2, 2, folder_to_save)

{'introduction': {'knn': KNeighborsClassifier(n_jobs=-1, n_neighbors=10)},
 'materials': {'knn': KNeighborsClassifier(n_jobs=-1, n_neighbors=10)},
 'conclusion': {'knn': KNeighborsClassifier(n_jobs=-1, n_neighbors=10)},
 'concat': {'knn': KNeighborsClassifier(n_jobs=-1, n_neighbors=10)}}

In [22]:
classifiers.pipeline_classifiers(
    dataset, parameters, sections, ['rf'],  -2, 2, folder_to_save)

{'introduction': {'rf': RandomForestClassifier(max_depth=10, min_samples_leaf=1000,
                         min_samples_split=2000, n_estimators=50, n_jobs=-1)},
 'materials': {'rf': RandomForestClassifier(max_depth=10, min_samples_leaf=1000,
                         min_samples_split=2000, n_estimators=50, n_jobs=-1)},
 'conclusion': {'rf': RandomForestClassifier(max_depth=2, min_samples_leaf=1000,
                         min_samples_split=2000, n_jobs=-1)},
 'concat': {'rf': RandomForestClassifier(max_depth=10, min_samples_leaf=1000,
                         min_samples_split=2000, n_estimators=25, n_jobs=-1)}}

In [23]:
classifiers.pipeline_classifiers(
    dataset, parameters, sections, ['ab'], 0, 2, folder_to_save)

{'introduction': {'ab': AdaBoostClassifier(n_estimators=100)},
 'materials': {'ab': AdaBoostClassifier(n_estimators=100)},
 'conclusion': {'ab': AdaBoostClassifier(n_estimators=100)},
 'concat': {'ab': AdaBoostClassifier(n_estimators=100)}}

In [35]:
classifiers.pipeline_classifiers(
    dataset, parameters, sections, ['cb'], 0, 2, folder_to_save)

cb


FileNotFoundError: [Errno 2] No such file or directory: 'models/test_/scratch/cinthiasouza/mv-text-summarizer/notebook/sv_models/cb_introduction.pkl'

In [11]:
classifiers.pipeline_classifiers(
    dataset, parameters, sections, ['gb'],  -2, 2, folder_to_save)

{'introduction': {'gb': GradientBoostingClassifier(min_samples_leaf=500, min_samples_split=1000,
                             n_estimators=10)},
 'materials': {'gb': GradientBoostingClassifier(min_samples_leaf=500, min_samples_split=1000,
                             n_estimators=10)},
 'conclusion': {'gb': GradientBoostingClassifier(min_samples_leaf=500, min_samples_split=1000,
                             n_estimators=10)},
 'concat': {'gb': GradientBoostingClassifier(min_samples_leaf=500, min_samples_split=1000,
                             n_estimators=10)}}

# Predict

In [24]:
from tensorflow.keras.models import model_from_json
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.metrics import Precision

In [25]:
def load_keras_model(section, path_to_save):

    json_file = open('{}/mlp_{}.json'.format(path_to_save, section), 'r')
    loaded_model_json = json_file.read()
    json_file.close()
    loaded_model = model_from_json(loaded_model_json)
    # load weights into new model
    loaded_model.load_weights('{}/mlp_{}.h5'.format(path_to_save, section))
    print("Loaded model from disk")
    
    loaded_model.compile(loss='categorical_crossentropy', optimizer=Adam(
                learning_rate=0.001), metrics=[Precision()])
    
    return loaded_model

In [26]:
def load_classifiers(sections, path_to_read, name_models):

    models = {}
    
    for section in sections:
        
        aux = {}
        
        for name_model in name_models:
            if name_model != 'mlp':
                aux[name_model] = joblib.load('{}/{}_{}.pkl'.format(path_to_read, name_model,  section))
            elif name_model == 'mlp':
                aux[name_model] = load_keras_model(section, path_to_read)
            
        models[section] = aux
        
    return models

In [34]:
sections=['introduction', 'materials', 'conclusion']
name_models = ['knn', 'rf', 'ab', 'cb' , 'gb']

models = load_classifiers(sections, path_to_save, name_models)

FileNotFoundError: [Errno 2] No such file or directory: '/scratch/cinthiasouza/mv-text-summarizer/notebook/sv_models/cb_introduction.pkl'

In [54]:
predictions, predictions_proba, results = ev.create_reports(models, dataset, columns_name, name_models, -1, 3, verbose=False)

In [ ]:
dr.display_results(results, section='introduction')

In [76]:
dr.display_results(results, section='materials')

knn_materials model precision recall f1-score support 
 
 0 
 knn 
 0.933884 
 0.794913 
 0.858813 
 27169.000000 
 
 
 1 
 knn 
 0.327784 
 0.639896 
 0.433506 
 4246.000000 
 
 
 accuracy 
 knn 
 0.773961 
 0.773961 
 0.773961 
 0.773961 
 
 
 macro avg 
 knn 
 0.630834 
 0.717405 
 0.646160 
 31415.000000 
 
 
 weighted avg 
 knn 
 0.851964 
 0.773961 
 0.801329 
 31415.000000 
 
            ab_materials model precision recall f1-score support 
 
 0 
 ab 
 0.944237 
 0.773455 
 0.850356 
 27169.000000 
 
 
 1 
 ab 
 0.328057 
 0.707725 
 0.448307 
 4246.000000 
 
 
 accuracy 
 ab 
 0.764571 
 0.764571 
 0.764571 
 0.764571 
 
 
 macro avg 
 ab 
 0.636147 
 0.740590 
 0.649331 
 31415.000000 
 
 
 weighted avg 
 ab 
 0.860955 
 0.764571 
 0.796016 
 31415.000000

rf_materials model precision recall f1-score support 
 
 0 
 rf 
 0.892408 
 0.992491 
 0.939793 
 27169.000000 
 
 
 1 
 rf 
 0.829858 
 0.234338 
 0.365473 
 4246.000000 
 
 
 accuracy 
 rf 
 0.890021 
 0.890021 
 0.890021 
 0.890021 
 
 
 macro avg 
 rf 
 0.861133 
 0.613415 
 0.652633 
 31415.000000 
 
 
 weighted avg 
 rf 
 0.883954 
 0.890021 
 0.862169 
 31415.000000 
 
            gb_materials model precision recall f1-score support 
 
 0 
 gb 
 0.945647 
 0.762045 
 0.843976 
 27169.000000 
 
 
 1 
 gb 
 0.320975 
 0.719736 
 0.443960 
 4246.000000 
 
 
 accuracy 
 gb 
 0.756327 
 0.756327 
 0.756327 
 0.756327 
 
 
 macro avg 
 gb 
 0.633311 
 0.740891 
 0.643968 
 31415.000000 
 
 
 weighted avg 
 gb 
 0.861217 
 0.756327 
 0.789911 
 31415.000000

mlp_materials model precision recall f1-score support 
 
 0 
 mlp 
 0.883585 
 0.999558 
 0.938001 
 27169.000000 
 
 
 1 
 mlp 
 0.982353 
 0.157325 
 0.271214 
 4246.000000 
 
 
 accuracy 
 mlp 
 0.885723 
 0.885723 
 0.885723 
 0.885723 
 
 
 macro avg 
 mlp 
 0.932969 
 0.578441 
 0.604607 
 31415.000000 
 
 
 weighted avg 
 mlp 
 0.896935 
 0.885723 
 0.847879 
 31415.000000 
 
            cb_materials model precision recall f1-score support 
 
 0 
 cb 
 0.892123 
 0.991682 
 0.939271 
 27169.000000 
 
 
 1 
 cb 
 0.813839 
 0.232690 
 0.361905 
 4246.000000 
 
 
 accuracy 
 cb 
 0.889098 
 0.889098 
 0.889098 
 0.889098 
 
 
 macro avg 
 cb 
 0.852981 
 0.612186 
 0.650588 
 31415.000000 
 
 
 weighted avg 
 cb 
 0.881542 
 0.889098 
 0.861235 
 31415.000000

In [77]:
dr.display_results(results, section='conclusion')

knn_conclusion model precision recall f1-score support 
 
 0 
 knn 
 0.960456 
 0.803848 
 0.875201 
 56140.000000 
 
 
 1 
 knn 
 0.220886 
 0.626908 
 0.326672 
 4980.000000 
 
 
 accuracy 
 knn 
 0.789431 
 0.789431 
 0.789431 
 0.789431 
 
 
 macro avg 
 knn 
 0.590671 
 0.715378 
 0.600936 
 61120.000000 
 
 
 weighted avg 
 knn 
 0.900197 
 0.789431 
 0.830508 
 61120.000000 
 
            ab_conclusion model precision recall f1-score support 
 
 0 
 ab 
 0.964930 
 0.789063 
 0.868180 
 56140.000000 
 
 
 1 
 ab 
 0.221536 
 0.676707 
 0.333796 
 4980.000000 
 
 
 accuracy 
 ab 
 0.779908 
 0.779908 
 0.779908 
 0.779908 
 
 
 macro avg 
 ab 
 0.593233 
 0.732885 
 0.600988 
 61120.000000 
 
 
 weighted avg 
 ab 
 0.904359 
 0.779908 
 0.824639 
 61120.000000

rf_conclusion model precision recall f1-score support 
 
 0 
 rf 
 0.930587 
 0.995582 
 0.961988 
 56140.000000 
 
 
 1 
 rf 
 0.765817 
 0.162851 
 0.268588 
 4980.000000 
 
 
 accuracy 
 rf 
 0.927732 
 0.927732 
 0.927732 
 0.927732 
 
 
 macro avg 
 rf 
 0.848202 
 0.579217 
 0.615288 
 61120.000000 
 
 
 weighted avg 
 rf 
 0.917162 
 0.927732 
 0.905491 
 61120.000000 
 
            gb_conclusion model precision recall f1-score support 
 
 0 
 gb 
 0.967629 
 0.768864 
 0.856871 
 56140.000000 
 
 
 1 
 gb 
 0.214147 
 0.710040 
 0.329053 
 4980.000000 
 
 
 accuracy 
 gb 
 0.764071 
 0.764071 
 0.764071 
 0.764071 
 
 
 macro avg 
 gb 
 0.590888 
 0.739452 
 0.592962 
 61120.000000 
 
 
 weighted avg 
 gb 
 0.906236 
 0.764071 
 0.813864 
 61120.000000

mlp_conclusion model precision recall f1-score support 
 
 0 
 mlp 
 0.936394 
 0.985999 
 0.960557 
 56140.000000 
 
 
 1 
 mlp 
 0.608175 
 0.244980 
 0.349270 
 4980.000000 
 
 
 accuracy 
 mlp 
 0.925622 
 0.925622 
 0.925622 
 0.925622 
 
 
 macro avg 
 mlp 
 0.772285 
 0.615490 
 0.654913 
 61120.000000 
 
 
 weighted avg 
 mlp 
 0.909651 
 0.925622 
 0.910750 
 61120.000000 
 
            cb_conclusion model precision recall f1-score support 
 
 0 
 cb 
 0.930897 
 0.995582 
 0.962154 
 56140.000000 
 
 
 1 
 cb 
 0.770158 
 0.166867 
 0.274303 
 4980.000000 
 
 
 accuracy 
 cb 
 0.928060 
 0.928060 
 0.928060 
 0.928060 
 
 
 macro avg 
 cb 
 0.850527 
 0.581225 
 0.618228 
 61120.000000 
 
 
 weighted avg 
 cb 
 0.917800 
 0.928060 
 0.906108 
 61120.000000

# Matthews Correlation

In [ ]:
df = ev.matthews(sections, dataset, predictions, name_models)
df